In [1]:
# conda install -c conda-forge dask-ml

In [2]:
# conda update -n base -c defaults conda

In [3]:
# !pip install dask-ml[complete]  --user 

In [53]:
import dask.dataframe as dd
import numpy as np
import pandas as pd
from sklearn.ensemble import RandomForestRegressor
from sklearn.model_selection import cross_validate, GridSearchCV
from sklearn.metrics import roc_auc_score
from dask_ml.model_selection import train_test_split
import pandas as pd
import joblib
import warnings

In [5]:
houses = dd.read_csv('c:/Users/Scott/jupyter/Class Activities/dennis mats/MLS_2017_to_2020.csv', 
                     dtype= {'# Tenants': 'object',
                               'Baths': 'float64',
                               'Bedrooms': 'float64',
                               'Condition.1': 'object',
                               'Half-Baths': 'float64',
                               'List Price / SqFt': 'object',
                               'Net Operating Income': 'object',
                               'Pool Y/N': 'object',
                               'Year Built': 'float64',
                               'Zoning': 'object'})

houses.columns = houses.columns.str.lower()
houses.columns = houses.columns.str.replace(' ', '_')

In [6]:
houses.dtypes

parcel_number                                 object
class                                         object
county                                        object
price                                         object
list_date                                     object
list_price                                    object
selling_price                                 object
selling_price.1                              float64
days_on_market                                 int64
days_on_mls                                    int64
closed_date                                   object
date_history_status                           object
price_/_sqft                                  object
list_price_/_sqft                             object
sold_price/sqft                               object
original_price                                object
date_price_change                             object
how_sold_code                                 object
address                                       

# General EDA

In [7]:
houses.head()

parcel_number class   county      price  list_date list_price  \
0  06600-012-003    AT  Alachua   $55,750   11/9/2017   $59,900    
1  07240-050-207    AT  Alachua  $108,000    3/2/2018  $115,000    
2  13199-010-011    AT  Alachua   $59,000   4/28/2017   $63,000    
3  06770-151-000    AT  Alachua   $55,000   1/13/2018   $56,000    
4  07242-090-007    AT  Alachua  $105,000    7/6/2019  $105,000    

  selling_price  selling_price.1  days_on_market  days_on_mls  ...  \
0      $55,750               NaN              33           33  ...   
1     $108,000               NaN              31           31  ...   
2      $59,000               NaN              88           88  ...   
3      $55,000               NaN              41           41  ...   
4     $105,000               NaN              18           18  ...   

  short_sale_y/n taxes_-_annual total_#_of_units #_of_garage_spaces  \
0             No          $859               NaN                NaN   
1             No        $1,676               NaN                NaN   
2             No        $1,070               NaN                NaN   
3             No        $1,022               NaN                NaN   
4             No        $1,329               NaN                NaN   

  garage_y/n net_operating_income pool_y/n zoning bank_owned_y/n auction  
0         No                  NaN      NaN    NaN             No      No  
1         No                  NaN      NaN    NaN             No      No  
2         No                  NaN      NaN    NaN             No      No  
3         No                  NaN      NaN    NaN             No      No  
4         No                  NaN      NaN    NaN             No      No  

[5 rows x 53 columns]

In [8]:
houses['class'].value_counts().compute()

RE    6908
AT    2401
CM     174
MF     145
Name: class, dtype: int64

Dropping some unneeded columns here

In [9]:
mls_df =  houses.drop(['selling_price.1', 'addtrentyn', '#_tenants', 
                        '#_floors', 'cap_rate_%', 'condition.1', 'date_leased', 'number_of_acres',
                        'pass_thru_exp/sf_annual', 'price/sqft_annual', 'price/sqft_monthly',
                        'total_#_of_units','net_operating_income'], axis=1)

mls_df.compute()

parcel_number class   county      price   list_date list_price  \
0     06600-012-003    AT  Alachua   $55,750    11/9/2017   $59,900    
1     07240-050-207    AT  Alachua  $108,000     3/2/2018  $115,000    
2     13199-010-011    AT  Alachua   $59,000    4/28/2017   $63,000    
3     06770-151-000    AT  Alachua   $55,000    1/13/2018   $56,000    
4     07242-090-007    AT  Alachua  $105,000     7/6/2019  $105,000    
...             ...   ...      ...        ...         ...        ...   
9623  07027-002-037    RE  Alachua  $451,920   10/12/2016  $445,700    
9624  07027-002-061    RE  Alachua  $339,440     2/8/2019  $309,942    
9625  07027-002-052    RE  Alachua  $359,423    8/14/2017  $352,837    
9626  07027-002-073    RE  Alachua  $332,105   10/16/2018  $329,843    
9627  07027-002-088    RE  Alachua  $316,251   10/27/2017  $299,000    

     selling_price  days_on_market  days_on_mls closed_date  ...  \
0         $55,750               33           33  12/12/2017  ...   
1        $108,000               31           31    4/2/2018  ...   
2         $59,000               88           88    8/3/2017  ...   
3         $55,000               41           41   2/23/2018  ...   
4        $105,000               18           18   7/24/2019  ...   
...            ...             ...          ...         ...  ...   
9623     $451,920              239          227    6/8/2017  ...   
9624     $339,440              203          199   8/30/2019  ...   
9625     $359,423              333          333   7/13/2018  ...   
9626     $332,105              248          248   6/21/2019  ...   
9627     $316,251              266          252   7/20/2018  ...   

     mls_only_entry_y/n_(no_services_provided) sale/rent short_sale_y/n  \
0                                           No  For Sale             No   
1                                           No  For Sale             No   
2                                          Yes  For Sale             No   
3                                           No  For Sale             No   
4                                           No  For Sale             No   
...                                        ...       ...            ...   
9623                                        No  For Sale             No   
9624                                        No  For Sale             No   
9625                                        No  For Sale             No   
9626                                        No  For Sale             No   
9627                                        No  For Sale             No   

     taxes_-_annual #_of_garage_spaces garage_y/n pool_y/n zoning  \
0             $859                 NaN         No      NaN    NaN   
1           $1,676                 NaN         No      NaN    NaN   
2           $1,070                 NaN         No      NaN    NaN   
3           $1,022                 NaN         No      NaN    NaN   
4           $1,329                 NaN         No      NaN    NaN   
...             ...                ...        ...      ...    ...   
9623          $660                   3        Yes       No    NaN   
9624          $664                   2        Yes       No    NaN   
9625          $655                   2        Yes       No    NaN   
9626          $654                   2        Yes       No    NaN   
9627          $653                   2        Yes       No    NaN   

     bank_owned_y/n auction  
0                No      No  
1                No      No  
2                No      No  
3                No      No  
4                No      No  
...             ...     ...  
9623             No      No  
9624             No      No  
9625             No      No  
9626             No      No  
9627             No      No  

[9628 rows x 40 columns]

Filtering the dataframe so it's only attached and residential classes

In [10]:
resmls_df = mls_df[mls_df['class'].isin(['AT', 'RE'])]

In [11]:
resmls_df['class'].value_counts().compute()

RE    6908
AT    2401
Name: class, dtype: int64

In [12]:
resmls_df.loc[:,['price_/_sqft','price', 'list_price','list_price_/_sqft', 'original_price', 'selling_price', 'sold_price/sqft']].head()

price_/_sqft      price list_price list_price_/_sqft original_price  \
0      $54.95    $55,750    $59,900                NaN       $59,900    
1      $98.12   $108,000   $115,000                NaN      $115,000    
2      $68.63    $59,000    $63,000                NaN       $63,000    
3      $45.68    $55,000    $56,000                NaN       $56,000    
4      $89.90   $105,000   $105,000                NaN      $105,000    

  selling_price sold_price/sqft  
0      $55,750          $51.15   
1     $108,000          $92.15   
2      $59,000          $64.27   
3      $55,000          $44.86   
4     $105,000          $89.90

I see some redundancy with price / selling_price and list_price / original_price. Since selling_price and list_price are clearer I'll drop price and original_price. I'm also planning on dropping list_price_/_sqft and price_/_sqft as it's hard to tell if they are redundant and are easy to calculate on my own (likely user input incosistencies)

In [13]:
resmls_df = resmls_df.drop(['price_/_sqft', 'price', 'list_price_/_sqft', 'original_price'], axis=1)

All of my prices are coming up as objects, likely due to the $. I'll need to strip and convert them to floats or ints before continuing my EDA

In [14]:
resmls_df.dtypes

parcel_number                                 object
class                                         object
county                                        object
list_date                                     object
list_price                                    object
selling_price                                 object
days_on_market                                 int64
days_on_mls                                    int64
closed_date                                   object
date_history_status                           object
sold_price/sqft                               object
date_price_change                             object
how_sold_code                                 object
address                                       object
city                                          object
state                                         object
zip_code                                      object
sfheatcool                                    object
year_built                                   f

In [15]:
# ['list_price','selling_price', 'sold_price/sqft']

In [16]:
resmls_df['selling_price'] = resmls_df['selling_price'].astype(str)

In [17]:
resmls_df['list_price'] = resmls_df['list_price'].apply(lambda x: x.replace('$', ''), meta = ('list_price', 'object'))
resmls_df['selling_price'] = resmls_df['selling_price'].apply(lambda x: x.replace('$', ''), meta = ('selling_price', 'object'))
resmls_df['sold_price/sqft'] = resmls_df['sold_price/sqft'].apply(lambda x: x.replace('$', ''), meta= ('sold_price/sqft', 'object'))

In [18]:
resmls_df['list_price'] = resmls_df['list_price'].apply(lambda x: x.replace(',', ''), meta = ('list_price', 'object')).astype(float)
resmls_df['selling_price'] = resmls_df['selling_price'].apply(lambda x: x.replace(',', ''), meta = ('selling_price', 'object')).astype(float)
resmls_df['sold_price/sqft'] = resmls_df['sold_price/sqft'].apply(lambda x: x.replace(',', ''), meta= ('sold_price/sqft', 'object')).astype(float)

In [19]:
resmls_df['sfheatcool'] = resmls_df['sfheatcool'].apply(lambda x: x.replace(',', ''), meta= ('sfheatcool', 'object')).astype(float)

In [20]:
resmls_df['list_sqft_price'] = (resmls_df['list_price'] / resmls_df['sfheatcool']).round(2)

## Dropping Columns cont: Redundant and/or Useless

In [21]:
resmls_df.columns

Index(['parcel_number', 'class', 'county', 'list_date', 'list_price',
       'selling_price', 'days_on_market', 'days_on_mls', 'closed_date',
       'date_history_status', 'sold_price/sqft', 'date_price_change',
       'how_sold_code', 'address', 'city', 'state', 'zip_code', 'sfheatcool',
       'year_built', 'baths', 'bedrooms', 'half-baths', 'condition',
       'listing_type', 'listing_visibility_type', 'for_comp_purposes_only_y/n',
       'mls_only_entry_y/n_(no_services_provided)', 'sale/rent',
       'short_sale_y/n', 'taxes_-_annual', '#_of_garage_spaces', 'garage_y/n',
       'pool_y/n', 'zoning', 'bank_owned_y/n', 'auction', 'list_sqft_price'],
      dtype='object')

In [22]:
resmls_df['for_comp_purposes_only_y/n'].value_counts().compute()

No     9194
Yes     113
Name: for_comp_purposes_only_y/n, dtype: int64

Going to drop columns that don't add any value to my analysis or are occuring as redundancies.

Sale/rent is useless since I pulled only residential sales data and no rental data. Listing type is also useless as it does little to impact sale price and only refers to the relationship between agent and seller. Listing visibility type only has one value and can be dropped for ease of analysis as well.

For comp purposes also doesn't mean much in this case since it's usually used for commercial properties that are sold off the mls. For residential, it means the house was sold by an agent but not on the mls. This won't impact sales price and can be dropped as a column.

As we can see below, the vast majority of MLS ONLY ENTRIES are 'No' and that input doesn't impact sales price much, it's just a reflection of marketing preference for the seller. The column can be dropped.

Annual Taxes is something else I can drop, as that has no bearing on sales price and because property taxes aren't a fixed value. Taxes get adjusted everytime there is a sale, and in Florida a homeowner can cap tax increases over the years. To put it simply, buyers shouldn't expect to pay the same taxes as the seller. b Auction as whole will be dropped, but first I plan on dropping the rows that indicate the property was sold in an auction since that will inevitably produce outliers that are not consistent with the rest of our sold data.

List date / sold date / days on mls / date history status / date price change can all be dropped as days on market provides all the information I need. Since list date and sold date can provide helpful insight later, I'm going to avoid dropping in place and plan on dropping them after other EDA has been completed.

In [23]:
resmls_df = resmls_df.drop(['sale/rent','days_on_mls', 'date_price_change', 'date_history_status', 
                          'listing_type', 'listing_visibility_type', 'for_comp_purposes_only_y/n', 
                          'mls_only_entry_y/n_(no_services_provided)', 'taxes_-_annual'], axis=1)

In [24]:
resmls_df['auction'].value_counts().compute()

No     9247
Yes      59
Name: auction, dtype: int64

In [25]:
resmls_df = resmls_df[resmls_df['auction'] == 'No']

In [26]:
resmls_df = resmls_df.drop('auction', axis=1)

### EDA on nulls

In [27]:
resmls_df.isna().mean().compute()*100

parcel_number          0.000000
class                  0.000000
county                 0.000000
list_date              0.000000
list_price             0.000000
selling_price          0.010814
days_on_market         0.000000
closed_date            0.010814
sold_price/sqft        0.000000
how_sold_code          0.032443
address                0.000000
city                   0.000000
state                  0.000000
zip_code               0.000000
sfheatcool             0.000000
year_built             0.010814
baths                  0.000000
bedrooms               0.000000
half-baths             0.000000
condition             38.023143
short_sale_y/n         0.000000
#_of_garage_spaces    39.591219
garage_y/n             0.000000
pool_y/n              25.813777
zoning                92.592192
bank_owned_y/n         0.000000
list_sqft_price        0.000000
dtype: float64

In [28]:
resmls_df.zoning.value_counts().compute()

RSF-1                     165
PD                        122
R-1A                       90
RSF-2                      69
RSF-3                      44
R-E Residential Estate     23
RE-1,aa,a,bb               21
R-1                        19
PUD                        17
A                          17
A-1                        12
R-1b                       11
RMF-5                      11
RSF-1,2                    10
RE                         10
RC                          6
AGR                         4
R-1C                        4
R-2                         3
R-1c                        3
R-1B                        3
PUD-1                       3
RSF-4                       3
R-3                         2
U2                          2
U6                          2
RH-1                        2
U9                          1
R1-C                        1
RSF-7                       1
U3                          1
ESA-2                       1
AG                          1
UMU-1     

From my own domain knowledge I can conclude that zoning isn't as important in residential valuation as it is for commercial. The only case it would be is if a house was zoned for a non-residential use case and was sold for a higher value (such as u6 or u9 zoning) which would would have the potential to create an outlier.

As seen in the above table, the "handy man special" UMU1 zoned property, which translates as a house in poor shape, was sold for a high price per squarefoot for cash. Also of note are the two U6 properties which were sold on he same date for the same amount - this indicates a portfolio sale of multiple properties and would be an outlier in my data set. These rows can be safely dropped from my data set.

In [29]:
resmls_df = resmls_df[(resmls_df['zoning'] != 'UMU-1') & (resmls_df['zoning'] != 'U9') 
                & (resmls_df['zoning'] != 'U6') & (resmls_df['zoning'] != 'U3') & (resmls_df['zoning'] != 'U2')]

In [30]:
resmls_df = resmls_df.drop('zoning', axis=1)

'# of garage spaces' is an interesting column with nulls since there is a second column with a categorical garage y/n that has no nulls associated with it. It should be a matter of determining if the nulls have a pattern with the garage y/n column and replacing the null if so.

In [31]:
resmls_df[resmls_df['#_of_garage_spaces'].isnull()].head(100)

parcel_number class   county  list_date  list_price  selling_price  \
0    06600-012-003    AT  Alachua  11/9/2017     59900.0        55750.0   
1    07240-050-207    AT  Alachua   3/2/2018    115000.0       108000.0   
2    13199-010-011    AT  Alachua  4/28/2017     63000.0        59000.0   
3    06770-151-000    AT  Alachua  1/13/2018     56000.0        55000.0   
4    07242-090-007    AT  Alachua   7/6/2019    105000.0       105000.0   
..             ...   ...      ...        ...         ...            ...   
117  06655-115-804    AT  Alachua   3/3/2018     53900.0        65000.0   
121  07294-110-003    AT  Alachua  6/10/2019     92500.0        83000.0   
122  07294-214-001    AT  Alachua  5/16/2019     75000.0        72500.0   
123  07332-201-019    AT  Alachua   6/4/2019     61000.0        55000.0   
124  07284-100-102    AT  Alachua  1/27/2019    145000.0       138000.0   

     days_on_market closed_date  sold_price/sqft how_sold_code  ... baths  \
0                33  12/12/2017            51.15          CASH  ...   1.0   
1                31    4/2/2018            92.15          CASH  ...   2.0   
2                88    8/3/2017            64.27  CONVENTIONAL  ...   1.0   
3                41   2/23/2018            44.86          CASH  ...   2.0   
4                18   7/24/2019            89.90          CASH  ...   2.0   
..              ...         ...              ...           ...  ...   ...   
117              11   3/14/2018            64.81          CASH  ...   2.0   
121              59    8/8/2019            83.00         OTHER  ...   1.0   
122              97   8/21/2019            73.83          CASH  ...   1.0   
123             132  10/14/2019           100.36          CASH  ...   1.0   
124              31   2/27/2019           117.25          CASH  ...   4.0   

    bedrooms half-baths condition  short_sale_y/n  #_of_garage_spaces  \
0        2.0        1.0       NaN              No                 NaN   
1        2.0        1.0       NaN              No                 NaN   
2        4.0        1.0       NaN              No                 NaN   
3        2.0        0.0       NaN              No                 NaN   
4        2.0        1.0     Other              No                 NaN   
..       ...        ...       ...             ...                 ...   
117      2.0        0.0     Other              No                 NaN   
121      2.0        1.0     Other              No                 NaN   
122      2.0        1.0     Other              No                 NaN   
123      1.0        0.0     Other              No                 NaN   
124      4.0        0.0     Other              No                 NaN   

     garage_y/n  pool_y/n  bank_owned_y/n list_sqft_price  
0            No       NaN              No           54.95  
1            No       NaN              No           98.12  
2            No       NaN              No           68.63  
3            No       NaN              No           45.68  
4            No       NaN              No           89.90  
..          ...       ...             ...             ...  
117          No       NaN              No           53.74  
121          No       NaN              No           92.50  
122          No       NaN              No           76.37  
123          No       NaN              No          111.31  
124          No       NaN              No          123.19  

[100 rows x 26 columns]

In [32]:
resmls_df['#_of_garage_spaces'] = resmls_df['#_of_garage_spaces'].fillna(0)

In [33]:
resmls_df['condition'].value_counts().compute()

Other                 4833
New Construction       664
Handyman Special       131
Under Construction      96
Name: condition, dtype: int64

In [34]:
resmls_df['condition'] = resmls_df['condition'].fillna('Other')

In [35]:
resmls_df['pool_y/n'].value_counts().compute()

No     5717
Yes    1136
Name: pool_y/n, dtype: int64

In [36]:
resmls_df['pool_y/n'] = resmls_df['pool_y/n'].fillna('No')

### lower % nulls

In [37]:
resmls_df['zip_code'].value_counts().compute()

32608         2697
32605         1554
32607         1248
32606         1115
32653          898
              ... 
32608-4147       1
32608-4134       1
32608-4105       1
32608-3613       1
30024            1
Name: zip_code, Length: 293, dtype: int64

In [38]:
resmls_df['zip_code'] = resmls_df['zip_code'].str.split('-').str[0]

In [39]:
resmls_df['zip_code'].value_counts().compute()

32608    2767
32605    1615
32607    1290
32606    1172
32653     930
32609     546
32601     517
32641     276
32603     101
32669       8
32615       5
32635       2
99999       1
32553       1
32604       1
32618       1
37607       1
32654       1
32657       1
32667       1
32697       1
35605       1
30024       1
Name: zip_code, dtype: int64

In [40]:
gainesville_zips = [32601, 32602, 32603, 32604, 32605, 32606, 32607, 32608, 32609, 32610, 32611,32612, 32641, 32653, 32635]

resmls_df['zip_code'] = resmls_df['zip_code'].astype(int)

resmls_df = resmls_df.loc[resmls_df['zip_code'].isin(gainesville_zips), :]

In [41]:
resmls_df['zip_code'].value_counts().compute()

32608    2767
32605    1615
32607    1290
32606    1172
32653     930
32609     546
32601     517
32641     276
32603     101
32635       2
32604       1
Name: zip_code, dtype: int64

In [42]:
reside_df = resmls_df.dropna()

In [43]:
reside_df.compute()

parcel_number class   county   list_date  list_price  selling_price  \
0     06600-012-003    AT  Alachua   11/9/2017     59900.0        55750.0   
1     07240-050-207    AT  Alachua    3/2/2018    115000.0       108000.0   
2     13199-010-011    AT  Alachua   4/28/2017     63000.0        59000.0   
3     06770-151-000    AT  Alachua   1/13/2018     56000.0        55000.0   
4     07242-090-007    AT  Alachua    7/6/2019    105000.0       105000.0   
...             ...   ...      ...         ...         ...            ...   
9623  07027-002-037    RE  Alachua  10/12/2016    445700.0       451920.0   
9624  07027-002-061    RE  Alachua    2/8/2019    309942.0       339440.0   
9625  07027-002-052    RE  Alachua   8/14/2017    352837.0       359423.0   
9626  07027-002-073    RE  Alachua  10/16/2018    329843.0       332105.0   
9627  07027-002-088    RE  Alachua  10/27/2017    299000.0       316251.0   

      days_on_market closed_date  sold_price/sqft how_sold_code  ... baths  \
0                 33  12/12/2017            51.15          CASH  ...   1.0   
1                 31    4/2/2018            92.15          CASH  ...   2.0   
2                 88    8/3/2017            64.27  CONVENTIONAL  ...   1.0   
3                 41   2/23/2018            44.86          CASH  ...   2.0   
4                 18   7/24/2019            89.90          CASH  ...   2.0   
...              ...         ...              ...           ...  ...   ...   
9623             239    6/8/2017           134.50          CASH  ...   4.0   
9624             203   8/30/2019           168.04            VA  ...   2.0   
9625             333   7/13/2018           170.34  CONVENTIONAL  ...   3.0   
9626             248   6/21/2019           195.36  CONVENTIONAL  ...   2.0   
9627             266   7/20/2018           156.56          USDA  ...   2.0   

     bedrooms half-baths           condition  short_sale_y/n  \
0         2.0        1.0               Other              No   
1         2.0        1.0               Other              No   
2         4.0        1.0               Other              No   
3         2.0        0.0               Other              No   
4         2.0        1.0               Other              No   
...       ...        ...                 ...             ...   
9623      6.0        1.0    New Construction              No   
9624      4.0        1.0  Under Construction              No   
9625      4.0        0.0    New Construction              No   
9626      3.0        0.0  Under Construction              No   
9627      4.0        1.0    New Construction              No   

      #_of_garage_spaces  garage_y/n  pool_y/n  bank_owned_y/n list_sqft_price  
0                      0          No        No              No           54.95  
1                      0          No        No              No           98.12  
2                      0          No        No              No           68.63  
3                      0          No        No              No           45.68  
4                      0          No        No              No           89.90  
...                  ...         ...       ...             ...             ...  
9623                   3         Yes        No              No          132.65  
9624                   2         Yes        No              No          153.44  
9625                   2         Yes        No              No          167.22  
9626                   2         Yes        No              No          194.03  
9627                   2         Yes        No              No          148.02  

[9213 rows x 26 columns]

In [44]:
reside_df.drop(['list_date', 'closed_date'], axis=1)

Dask DataFrame Structure:
              parcel_number   class  county list_price selling_price days_on_market sold_price/sqft how_sold_code address    city   state zip_code sfheatcool year_built    baths bedrooms half-baths condition short_sale_y/n #_of_garage_spaces garage_y/n pool_y/n bank_owned_y/n list_sqft_price
npartitions=1                                                                                                                                                                                                                                                                                       
                     object  object  object    float64       float64          int64         float64        object  object  object  object    int32    float64    float64  float64  float64    float64    object         object             object     object   object         object         float64
                        ...     ...     ...        ...           ...            ...             ...           ...     ...     ...     ...      ...        ...        ...      ...      ...        ...       ...            ...                ...        ...      ...            ...             ...
Dask Name: drop_by_shallow_copy, 84 tasks

In [49]:
dummy = dd.get_dummies(reside_df.categorize())

In [52]:
dummy

Dask DataFrame Structure:
              list_price selling_price days_on_market sold_price/sqft zip_code sfheatcool year_built    baths bedrooms half-baths list_sqft_price parcel_number_06600-012-003 parcel_number_07240-050-207 parcel_number_13199-010-011 parcel_number_06770-151-000 parcel_number_07242-090-007 parcel_number_06685-119-003 parcel_number_09013-033-001 parcel_number_6770209000 parcel_number_06126-042-000 parcel_number_09013-033-002 parcel_number_07240-050-503 parcel_number_08992-032-019 parcel_number_09003-018-143 parcel_number_13199-010- parcel_number_13199-010-010 parcel_number_6860170176 parcel_number_07305-001-006 parcel_number_06853-102-202 parcel_number_06853-117-203 parcel_number_09008-010-005 parcel_number_13199-010-053 parcel_number_06877-121-003 parcel_number_07242-070-008 parcel_number_13199-010-019 parcel_number_06655-113-604 parcel_number_06750-010-003 parcel_number_06860-516-301 parcel_number_06680-010-061 parcel_number_06680-103-085 parcel_number_06680-031-005 parcel_number_14956-311-000 parcel_number_09003-011-261 parcel_number_06234-240-005 parcel_number_12195-001-002 parcel_number_13199-010-018 parcel_number_09003-003-185 parcel_number_06234-250-023 parcel_number_13199-010-014 parcel_number_ 13199-010-034 parcel_number_06655-113-606 parcel_number_06724-103-301 parcel_number_06853-121-202 parcel_number_06860-150-088 parcel_number_09013-011-041 parcel_number_06579-054-053 parcel_number_06877-138-002 parcel_number_06500-133-000 parcel_number_06500-163-000 parcel_number_06701-108-000 parcel_number_06680-020-021 parcel_number_07285-001-216 parcel_number_09013-011-013 parcel_number_06860-170-067 parcel_number_06076-053-037 parcel_number_06237-015-002 parcel_number_09013-011-051 parcel_number_09003-010-256 parcel_number_09009-010-267 parcel_number_06819-020-119 parcel_number_6680010009 parcel_number_08160-005-021 parcel_number_06757-005-125 parcel_number_9013208002 parcel_number_6099010030 parcel_number_06500-144-000 parcel_number_06500-231-000 parcel_number_06500-316-000 parcel_number_6655114706 parcel_number_07294-202-023 parcel_number_06579-053-033 parcel_number_09013-011-032 parcel_number_06735-139-002 parcel_number_14552-903-000 parcel_number_06655-100-115 parcel_number_06735-123-004 parcel_number_06853-115-302 parcel_number_7296030049 parcel_number_07297-021-005 parcel_number_07891-030-233 parcel_number_06126-027-000 parcel_number_06237-016-001 parcel_number_07305-003-005 parcel_number_ 09013-011-054 parcel_number_06765-080-805 parcel_number_06860-040-006 parcel_number_06077-100-013 parcel_number_06686-059-000 parcel_number_06680-031-017 parcel_number_06685-114-001 parcel_number_06386-010-049 parcel_number_09762-012-000 parcel_number_14567-040-417 parcel_number_07284-400-308 parcel_number_06655-100-151 parcel_number_06877-433-002 parcel_number_07284-300-205 parcel_number_07297-010-106 parcel_number_09009-010-217 parcel_number_07242-070-006 parcel_number_06680-101-018 parcel_number_SW 43rd Street to the en parcel_number_07300-501-000 parcel_number_6126 parcel_number_06735-108-003 parcel_number_06850-028-014 parcel_number_06735-145-002 parcel_number_06819-020-042 parcel_number_06680-030-017 parcel_number_06500-329-000 parcel_number_07294-114-003 parcel_number_07242-090-008 parcel_number_06685-104-002 parcel_number_6500330000 parcel_number_6655503007 parcel_number_15633-064-004 parcel_number_06653-029-000 parcel_number_06655-115-804 parcel_number_06860-170-070 parcel_number_07929-101-001 parcel_number_07929-117-047 parcel_number_07294-110-003 parcel_number_07294-214-001 parcel_number_07332-201-019 parcel_number_07284-100-102 parcel_number_06539-101-002 parcel_number_07294-211-008 parcel_number_07300-802-000 parcel_number_07301-605-000 parcel_number_06877-439-004 parcel_number_06017-013-031 parcel_number_06680-010-025 parcel_number_06680-030-021 parcel_number_06680-030-036 parcel_number_06750-010-005 parcel_number_06500-318-000 parcel_number_07284-600-106 parcel_number_07294-202-326 parcel_number_0733

In [54]:
# This is our feature set
X = dummy.drop(['sold_price/sqft','selling_price', 'list_price'], axis=1)

# This is our target variable
Y = dummy["selling_price"]

X_train, X_test, y_train, y_test = train_test_split(X, Y, test_size=0.2)

# Since our data can fit into memory
# we persist them to the RAM.
X_train.persist()
X_test.persist()
y_train.persist()
y_test.persist()

C:\Users\Scott\AppData\Roaming\Python\Python37\site-packages\dask_ml\model_selection\_split.py:469: FutureWarning: The default value for 'shuffle' must be specified when splitting DataFrames. In the future DataFrames will automatically be shuffled within blocks prior to splitting. Specify 'shuffle=True' to adopt the future behavior now, or 'shuffle=False' to retain the previous behavior.
  category=FutureWarning,


Dask Series Structure:
npartitions=1
    float64
        ...
Name: selling_price, dtype: float64
Dask Name: split, 1 tasks

In [57]:
from dask.distributed import Client

client = Client()

rf_model = RandomForestRegressor()

with joblib.parallel_backend('dask'):
    scores = cross_validate(rf_model, X_train.compute(), y_train.compute(), cv=4)
    
scores

S:\Anaconda\lib\site-packages\distributed\dashboard\core.py:79: UserWarning: 
Port 8787 is already in use. 
Perhaps you already have a cluster running?
Hosting the diagnostics dashboard on a random port instead.
  warnings.warn("\n" + msg)


{'fit_time': array([196.29456997, 195.03594208, 199.31054091, 198.22393608]),
 'score_time': array([1.00367117, 0.83672404, 0.7847414 , 1.12763143]),
 'test_score': array([0.98229338, 0.97230317, 0.9965098 , 0.99219054])}

In [58]:
rf_params = {"max_depth": [2, 4, 8, 16]}

rf_model = RandomForestRegressor()

grid_search_rf = GridSearchCV(rf_model,
                           param_grid=rf_params,
                           return_train_score=True,
                           iid=True,
                           cv=4,
                           n_jobs=-1, 
                           scoring='r2')

In [59]:
with joblib.parallel_backend('dask'):
    grid_search_rf.fit(X_train.compute(), y_train.compute())

S:\Anaconda\lib\site-packages\sklearn\model_selection\_search.py:823: FutureWarning: The parameter 'iid' is deprecated in 0.22 and will be removed in 0.24.
  "removed in 0.24.", FutureWarning


In [60]:
print("The best value is: ", grid_search_rf.best_params_)
print("The test r2 score is: ", grid_search_rf.score(X_test.compute(), y_test.compute()))

The best value is:  {'max_depth': 16}
The test r2 score is:  0.9483652442402727
